
# IBM Applied Data Science Capstone Course by Coursera

###   Opening a New Shopping Mall in  Bengaluru , India

    - Build a dataframe of neighborhoods in Bengaluru, India by web scraping the data from Wikipedia page
    - Get the geographical coordinates of the neighborhoods
    - Obtain the venue data for the neighborhoods from Foursquare API
    - Explore and cluster the neighborhoods
    - Select the best cluster to open a new shopping mall

### Import Libraries

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
!pip install geocoder
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium
import folium # map rendering library

print("Libraries imported.")

     |████████████████████████████████| 102kB 18.4MB/s ta 0:00:01
     |████████████████████████████████| 92kB 8.6MB/s eta 0:00:011
Libraries imported.


## 2. Scrap data from Wikipedia page into a DataFrame

In [3]:
# send the GET request
data = requests.get("https://en.wikipedia.org/wiki/Category:Neighbourhoods_in_Bangalore").text

In [4]:
# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(data, 'html.parser')

In [5]:
# create a list to store neighborhood data
neighborhoodList = []

# append the data into the list
for row in soup.find_all("div", class_="mw-category")[0].findAll("li"):
    neighborhoodList.append(row.text)

In [6]:
# create a new DataFrame from the list
df = pd.DataFrame({"Neighborhood": neighborhoodList})
df.head()

Neighborhood
0  List of areas in Bangalore Cantonment
1        List of areas in Bengaluru Pete
2    List of neighbourhoods in Bangalore
3                                Adugodi
4                       Agara, Bangalore

In [7]:
df.drop(df.head(3).index, inplace=True)
df.reset_index(drop=True, inplace=True)
df.head()

Neighborhood
0           Adugodi
1  Agara, Bangalore
2       Ananthnagar
3        Anjanapura
4           Arekere

In [8]:
df.shape

(129, 1)

### Get the geographical coordinates

In [9]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Bangalore, Karnataka, India'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords


In [10]:
# call the function to get the coordinates, store in a new list using list comprehension
cooodinates = [ get_latlng(neighborhood) for neighborhood in df["Neighborhood"].tolist() ]

In [11]:
cooodinates

[[12.944020000000023, 77.60800000000006],
 [12.842830000000049, 77.48759000000007],
 [12.954080000000033, 77.54135000000008],
 [12.858110000000067, 77.55909000000008],
 [12.885680000000036, 77.59668000000005],
 [12.963480000000061, 77.61297000000008],
 [13.02753000000007, 77.65049000000005],
 [13.07728748449913, 77.65760577036913],
 [13.044710000000066, 77.55008000000004],
 [12.922310000000039, 77.56988000000007],
 [13.019643510687336, 77.65469211693214],
 [12.938980000000072, 77.57137000000006],
 [12.992220000000032, 77.53444000000007],
 [12.927350000000047, 77.67185000000006],
 [13.083010000000058, 77.54779000000008],
 [12.900090000000034, 77.60433000000006],
 [12.903080000000045, 77.62444000000005],
 [12.817530000000033, 77.67879000000005],
 [12.993330000000071, 77.66123000000005],
 [12.91488000000004, 77.61004000000008],
 [12.951940000000036, 77.54445000000004],
 [12.913110000000074, 77.71565000000004],
 [12.959700296061198, 77.57131179631511],
 [12.794010000000071, 77.700150000000

In [12]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coordinates = pd.DataFrame(cooodinates, columns=['Latitude', 'Longitude'])

In [13]:
# merge the coordinates into the original dataframe
df['Latitude'] = df_coordinates['Latitude']
df['Longitude'] = df_coordinates['Longitude']
# check the neighborhoods and the coordinates
print(df.shape)
df

(129, 3)


Neighborhood   Latitude  Longitude
0                                Adugodi  12.944020  77.608000
1                       Agara, Bangalore  12.842830  77.487590
2                            Ananthnagar  12.954080  77.541350
3                             Anjanapura  12.858110  77.559090
4                                Arekere  12.885680  77.596680
5                            Austin Town  12.963480  77.612970
6                            Babusapalya  13.027530  77.650490
7               Bagalur, Bangalore Urban  13.077287  77.657606
8                          Bahubalinagar  13.044710  77.550080
9                           Banashankari  12.922310  77.569880
10                             Banaswadi  13.019644  77.654692
11                          Basavanagudi  12.938980  77.571370
12                     Basaveshwaranagar  12.992220  77.534440
13                             Bellandur  12.927350  77.671850
14                          Bharathnagar  13.083010  77.547790
15                           Bilekahalli  12.900090  77.604330
16                          Bommanahalli  12.903080  77.624440
17                           Bommasandra  12.817530  77.678790
18                           Brookefield  12.993330  77.661230
19                            BTM Layout  12.914880  77.610040
20                       Byatarayanapura  12.951940  77.544450
21                            Carmelaram  12.913110  77.715650
22                            Chamrajpet  12.959700  77.571312
23                            Chandapura  12.794010  77.700150
24                              Chickpet  12.970150  77.575890
25                        Chikkalasandra  12.909950  77.550510
26                            Cooke Town  13.003630  77.622830
27                   Cox Town, Bangalore  12.995940  77.626440
28                        CV Raman Nagar  12.979019  77.656138
29                           Dasarahalli  13.042240  77.515070
30                   Devarachikkanahalli  12.888330  77.617640
31                        Dollars Colony  13.040250  77.569090
32                                Domlur  12.943290  77.656020
33                               Ejipura  12.946970  77.625590
34                       Electronic City  12.845470  77.664300
35                Fraser Town, Bangalore  12.998940  77.612760
36                         Gandhi Bazaar  12.944780  77.572130
37               Gandhi Nagar, Bangalore  13.026430  77.617740
38                 Ganganagar, Bangalore  13.014450  77.588080
39                             Girinagar  12.942790  77.541220
40                          Gowdanapalya  12.909680  77.556750
41            Hanumanthanagar, Bengaluru  12.943720  77.561200
42                            HBR Layout  13.026420  77.624370
43                             Hebbagodi  12.830840  77.680340
44                                Hebbal  13.049810  77.589030
45                                 Hoodi  12.991980  77.715060
46                              Horamavu  13.038700  77.661920
47                            HSR Layout  12.912160  77.644900
48                              Hulimavu  12.880640  77.601470
49                           Immadihalli  12.966860  77.761580
50                           Indiranagar  13.030060  77.495260
51                              Ittamadu  12.923440  77.542840
52                           J. P. Nagar  12.908310  77.590240
53                                Jakkur  13.075640  77.603940
54                             Jalahalli  13.054500  77.526580
55                  Jayanagar, Bangalore  12.928720  77.582810
56                    Jeevanbheema Nagar  12.966010  77.657670
57                                Jigani  12.781130  77.642580
58                         Kaggadasapura  12.965530  77.666660
59                          Kalasipalyam  12.961840  77.574780
60                           Kalikanagar  13.010630  77.490700
61                               Kalkere  13.034030  77.675110
62                          Kalyan Nagar  12.968020  77.521

In [14]:
# get the coordinates of Bengaluru
address = 'Bengaluru, India'

geolocator = Nominatim(user_agent="my-app")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Bengaluru, India {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Bengaluru, India 12.9791198, 77.5912997.


In [15]:

# create map of Bengaluru using latitude and longitude values
map_BLR = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(df['Latitude'], df['Longitude'], df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_BLR)  
    
map_BLR

In [16]:
# save the map as HTML file
map_BLR.save('map_BLR.html')

### 5. Use the Foursquare API to explore the neighborhoods

In [41]:
# define Foursquare Credentials and Version
CLIENT_ID = '***' # your Foursquare ID
CLIENT_SECRET = '***' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' "****")
print('CLIENT_SECRET:' "***")

Your credentails:
CLIENT_ID: ****
CLIENT_SECRET:***


#### Now, let's get the top 100 venues that are within a radius of 2000 meters

In [19]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(df['Latitude'], df['Longitude'], df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [20]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(6798, 7)


Neighborhood  Latitude  Longitude               VenueName  VenueLatitude  \
0      Adugodi  12.94402     77.608                PVR IMAX      12.934595   
1      Adugodi  12.94402     77.608          Tommy Hilfiger      12.934552   
2      Adugodi  12.94402     77.608    Truffles Ice & Spice      12.933443   
3      Adugodi  12.94402     77.608             PVR Cinemas      12.934389   
4      Adugodi  12.94402     77.608  Zingron - Naga Kitchen      12.936271   

   VenueLongitude      VenueCategory  
0       77.611321      Movie Theater  
1       77.611347     Clothing Store  
2       77.614265       Burger Joint  
3       77.611184          Multiplex  
4       77.615051  Indian Restaurant

In [22]:
venues_df

Neighborhood   Latitude  Longitude  \
0                                 Adugodi  12.944020  77.608000   
1                                 Adugodi  12.944020  77.608000   
2                                 Adugodi  12.944020  77.608000   
3                                 Adugodi  12.944020  77.608000   
4                                 Adugodi  12.944020  77.608000   
5                                 Adugodi  12.944020  77.608000   
6                                 Adugodi  12.944020  77.608000   
7                                 Adugodi  12.944020  77.608000   
8                                 Adugodi  12.944020  77.608000   
9                                 Adugodi  12.944020  77.608000   
10                                Adugodi  12.944020  77.608000   
11                                Adugodi  12.944020  77.608000   
12                                Adugodi  12.944020  77.608000   
13                                Adugodi  12.944020  77.608000   
14                                Adugodi  12.944020  77.608000   
15                                Adugodi  12.944020  77.608000   
16                                Adugodi  12.944020  77.608000   
17                                Adugodi  12.944020  77.608000   
18                                Adugodi  12.944020  77.608000   
19                                Adugodi  12.944020  77.608000   
20                                Adugodi  12.944020  77.608000   
21                                Adugodi  12.944020  77.608000   
22                                Adugodi  12.944020  77.608000   
23                                Adugodi  12.944020  77.608000   
24                                Adugodi  12.944020  77.608000   
25                                Adugodi  12.944020  77.608000   
26                                Adugodi  12.944020  77.608000   
27                                Adugodi  12.944020  77.608000   
28                                Adugodi  12.944020  77.608000   
29                                Adugodi  12.944020  77.608000   
30                                Adugodi  12.944020  77.608000   
31                                Adugodi  12.944020  77.608000   
32                                Adugodi  12.944020  77.608000   
33                                Adugodi  12.944020  77.608000   
34                                Adugodi  12.944020  77.608000   
35                                Adugodi  12.944020  77.608000   
36                                Adugodi  12.944020  77.608000   
37                                Adugodi  12.944020  77.608000   
38                                Adugodi  12.944020  77.608000   
39                                Adugodi  12.944020  77.608000   
40                                Adugodi  12.944020  77.608000   
41                                Adugodi  12.944020  77.608000   
42                                Adugodi  12.944020  77.608000   
43                                Adugodi  12.944020  77.608000   
44                                Adugodi  12.944020  77.608000   
45                                Adugodi  12.944020  77.608000   
46                                Adugodi  12.944020  77.608000   
47                                Adugodi  12.944020  77.608000   
48                                Adugodi  12.944020  77.608000   
49                                Adugodi  12.944020  77.608000   
50                                Adugodi  12.944020  77.608000   
51                                Adugodi  12.944020  77.608000   
52                                Adugodi  12.944020  77.608000   
53                                Adugodi  12.944020  77.608000   
54                                Adugodi  12.944020  77.608000   
55                                Adugodi  12.944020  77.608000   
56                                Adugodi  12.944020  77.608000   
57                                Adugodi  12.944020  77.608000   
58                                Adugodi  12.944020  77.608000   
59       

#### Let's check how many venues were returned for each neighorhood

In [23]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  \
Neighborhood                                                          
Adugodi                                   100        100        100   
Ananthnagar                                30         30         30   
Anjanapura                                  4          4          4   
Arekere                                    77         77         77   
Austin Town                               100        100        100   
BTM Layout                                 84         84         84   
Babusapalya                                48         48         48   
Bagalur, Bangalore Urban                    9          9          9   
Bahubalinagar                              23         23         23   
Banashankari                              100        100        100   
Banaswadi                                  52         52         52   
Basavanagudi                              100        100        100   
Basaveshwaranagar                          39         39         39   
Bellandur                                  89         89         89   
Bharathnagar                                7          7          7   
Bilekahalli                                93         93         93   
Bommanahalli                               62         62         62   
Bommasandra                                 7          7          7   
Brookefield                                42         42         42   
Byatarayanapura                            42         42         42   
CV Raman Nagar                            100        100        100   
Carmelaram                                  5          5          5   
Chamrajpet                                 80         80         80   
Chandapura                                  4          4          4   
Chickpet                                   72         72         72   
Chikkalasandra                             36         36         36   
Cooke Town                                 72         72         72   
Cox Town, Bangalore                        72         72         72   
Dasarahalli                                10         10         10   
Devarachikkanahalli                        19         19         19   
Dollars Colony                             66         66         66   
Domlur                                     48         48         48   
Ejipura                                    78         78         78   
Electronic City                            48         48         48   
Fraser Town, Bangalore                     93         93         93   
Gandhi Bazaar                              99         99         99   
Gandhi Nagar, Bangalore                    22         22         22   
Ganganagar, Bangalore                      75         75         75   
Girinagar                                  32         32         32   
Gowdanapalya                               55         55         55   
HBR Layout                                 60         60         60   
HSR Layout                                 64         64         64   
Hanumanthanagar, Bengaluru                 79         79         79   
Hebbagodi                                  15         15         15   
Hebbal                                     45         45         45   
Hoodi                                      43         43         43   
Horamavu                                    5          5          5   
Hulimavu                                   59         59         59   
Immadihalli                                36         36         36   
Indiranagar                                 4          4          4   
Ittamadu                                   39         39         39   
J. P. Nagar                               100        100        100   
Jakkur                                     14         14         14   
Jalahalli                                   8          8          8   
Jayanagar, Bangalore                      100        100     

#### Let's find out how many unique categories can be curated from all the returned venues

In [24]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 237 uniques categories.


In [25]:
# print out the list of categories
venues_df['VenueCategory'].unique()[:50]

array(['Movie Theater', 'Clothing Store', 'Burger Joint', 'Multiplex',
       'Indian Restaurant', 'Financial or Legal Service', 'Lounge',
       'Creperie', 'Brewery', 'Donut Shop', 'Breakfast Spot', 'Café',
       'Tea Room', 'Shopping Mall', 'Bar', 'Gym', 'Ice Cream Shop',
       'Dessert Shop', 'Juice Bar', 'Coffee Shop', 'Mobile Phone Shop',
       'Italian Restaurant', 'Bookstore', 'Arcade', 'Bakery',
       'Chinese Restaurant', 'Indian Sweet Shop', 'Gaming Cafe',
       'Yoga Studio', 'Smoke Shop', "Men's Store", 'Punjabi Restaurant',
       'Andhra Restaurant', 'Paper / Office Supplies Store',
       'Pizza Place', 'Thai Restaurant', 'Kerala Restaurant',
       'Cosmetics Shop', 'Mexican Restaurant', 'Salon / Barbershop',
       'Comfort Food Restaurant', 'Food Court', 'Bowling Alley',
       'Middle Eastern Restaurant', 'Persian Restaurant',
       'Eastern European Restaurant', 'Tibetan Restaurant',
       'Electronics Store', 'Liquor Store', 'Seafood Restaurant'],
      dty

In [26]:
# check if the results contain "Shopping Mall"
"Neighborhood" in venues_df['VenueCategory'].unique()

True

### 6. Analyze Each Neighborhood

In [27]:
# one hot encoding
BLR_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
BLR_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [BLR_onehot.columns[-1]] + list(BLR_onehot.columns[:-1])
BLR_onehot = BLR_onehot[fixed_columns]

print(BLR_onehot.shape)
BLR_onehot.head()

(6798, 238)


Neighborhoods  ATM  Accessories Store  Afghan Restaurant  Airport  \
0       Adugodi    0                  0                  0        0   
1       Adugodi    0                  0                  0        0   
2       Adugodi    0                  0                  0        0   
3       Adugodi    0                  0                  0        0   
4       Adugodi    0                  0                  0        0   

   American Restaurant  Andhra Restaurant  Arcade  Art Gallery  Art Museum  \
0                    0                  0       0            0           0   
1                    0                  0       0            0           0   
2                    0                  0       0            0           0   
3                    0                  0       0            0           0   
4                    0                  0       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0                    0                 0                   0   
1                    0                 0                   0   
2                    0                 0                   0   
3                    0                 0                   0   
4                    0                 0                   0   

   Australian Restaurant  Auto Garage  Auto Workshop  BBQ Joint  \
0                      0            0              0          0   
1                      0            0              0          0   
2                      0            0              0          0   
3                      0            0              0          0   
4                      0            0              0          0   

   Badminton Court  Bagel Shop  Bakery  Bar  Basketball Court  \
0                0           0       0    0                 0   
1                0           0       0    0                 0   
2                0           0       0    0                 0   
3                0           0       0    0                 0   
4                0           0       0    0                 0   

   Bed & Breakfast  Beer Garden  Bengali Restaurant  Big Box Store  Bike Shop  \
0                0            0                   0              0          0   
1                0            0                   0              0          0   
2                0            0                   0              0          0   
3                0            0                   0              0          0   
4                0            0                   0              0          0   

   Bistro  Boarding House  Boat or Ferry  Bookstore  Botanical Garden  \
0       0               0              0          0                 0   
1       0               0              0          0                 0   
2       0               0              0          0                 0   
3       0               0              0          0                 0   
4       0               0              0          0                 0   

   Boutique  Bowling Alley  Breakfast Spot  Brewery  Bridge  Bubble Tea Shop  \
0         0              0               0        0       0                0   
1         0              0               0        0       0                0   
2         0              0               0        0       0                0   
3         0              0               0        0       0                0   
4         0              0               0        0       0                0   

   Building  Burger Joint  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0         0             0              0         0            0         0   
1         0             0              0         0            0         0   
2         0             1              0         0            0         0   
3         0             0              0         0            0         0   
4         0             0              0         0            0         0   

   Business Service  Butcher  Cafeteria  Café  Campground

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [28]:
BLR_grouped = BLR_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(BLR_grouped.shape)
BLR_grouped

(128, 238)


Neighborhoods       ATM  Accessories Store  \
0                                Adugodi  0.000000           0.000000   
1                            Ananthnagar  0.000000           0.000000   
2                             Anjanapura  0.250000           0.000000   
3                                Arekere  0.000000           0.000000   
4                            Austin Town  0.000000           0.000000   
5                             BTM Layout  0.000000           0.000000   
6                            Babusapalya  0.000000           0.000000   
7               Bagalur, Bangalore Urban  0.000000           0.000000   
8                          Bahubalinagar  0.000000           0.000000   
9                           Banashankari  0.000000           0.000000   
10                             Banaswadi  0.000000           0.000000   
11                          Basavanagudi  0.000000           0.000000   
12                     Basaveshwaranagar  0.000000           0.000000   
13                             Bellandur  0.000000           0.000000   
14                          Bharathnagar  0.000000           0.000000   
15                           Bilekahalli  0.000000           0.000000   
16                          Bommanahalli  0.000000           0.000000   
17                           Bommasandra  0.000000           0.000000   
18                           Brookefield  0.000000           0.000000   
19                       Byatarayanapura  0.000000           0.000000   
20                        CV Raman Nagar  0.000000           0.000000   
21                            Carmelaram  0.000000           0.000000   
22                            Chamrajpet  0.000000           0.000000   
23                            Chandapura  0.000000           0.000000   
24                              Chickpet  0.000000           0.000000   
25                        Chikkalasandra  0.000000           0.027778   
26                            Cooke Town  0.000000           0.000000   
27                   Cox Town, Bangalore  0.000000           0.000000   
28                           Dasarahalli  0.000000           0.000000   
29                   Devarachikkanahalli  0.000000           0.000000   
30                        Dollars Colony  0.000000           0.000000   
31                                Domlur  0.000000           0.000000   
32                               Ejipura  0.000000           0.000000   
33                       Electronic City  0.000000           0.000000   
34                Fraser Town, Bangalore  0.000000           0.000000   
35                         Gandhi Bazaar  0.000000           0.000000   
36               Gandhi Nagar, Bangalore  0.000000           0.000000   
37                 Ganganagar, Bangalore  0.000000           0.000000   
38                             Girinagar  0.000000           0.000000   
39                          Gowdanapalya  0.000000           0.018182   
40                            HBR Layout  0.000000           0.000000   
41                            HSR Layout  0.000000           0.000000   
42            Hanumanthanagar, Bengaluru  0.000000           0.000000   
43                             Hebbagodi  0.000000           0.000000   
44                                Hebbal  0.000000           0.022222   
45                                 Hoodi  0.000000           0.000000   
46                              Horamavu  0.000000           0.000000   
47                              Hulimavu  0.000000           0.000000   
48                           Immadihalli  0.000000           0.000000   
49                           Indiranagar  0.500000           0.000000   
50                              Ittamadu  0.000000           0.025641   
51                           J. P. Nagar  0.000000           0.000000   
52                                Jakkur  0.000000           0.000000   
53                             Jalahalli  0.000000           0.000000   
54          

In [29]:
len(BLR_grouped[BLR_grouped["Shopping Mall"] > 0])

58

#### Create a new DataFrame for Shopping Mall data only

In [30]:
BLR_mall = BLR_grouped[["Neighborhoods","Shopping Mall"]]
BLR_mall

Neighborhoods  Shopping Mall
0                                Adugodi       0.010000
1                            Ananthnagar       0.000000
2                             Anjanapura       0.000000
3                                Arekere       0.025974
4                            Austin Town       0.010000
5                             BTM Layout       0.011905
6                            Babusapalya       0.000000
7               Bagalur, Bangalore Urban       0.000000
8                          Bahubalinagar       0.000000
9                           Banashankari       0.010000
10                             Banaswadi       0.000000
11                          Basavanagudi       0.000000
12                     Basaveshwaranagar       0.000000
13                             Bellandur       0.011236
14                          Bharathnagar       0.000000
15                           Bilekahalli       0.010753
16                          Bommanahalli       0.000000
17                           Bommasandra       0.000000
18                           Brookefield       0.023810
19                       Byatarayanapura       0.000000
20                        CV Raman Nagar       0.010000
21                            Carmelaram       0.000000
22                            Chamrajpet       0.012500
23                            Chandapura       0.000000
24                              Chickpet       0.013889
25                        Chikkalasandra       0.027778
26                            Cooke Town       0.027778
27                   Cox Town, Bangalore       0.027778
28                           Dasarahalli       0.100000
29                   Devarachikkanahalli       0.000000
30                        Dollars Colony       0.000000
31                                Domlur       0.000000
32                               Ejipura       0.000000
33                       Electronic City       0.000000
34                Fraser Town, Bangalore       0.021505
35                         Gandhi Bazaar       0.000000
36               Gandhi Nagar, Bangalore       0.000000
37                 Ganganagar, Bangalore       0.000000
38                             Girinagar       0.000000
39                          Gowdanapalya       0.036364
40                            HBR Layout       0.000000
41                            HSR Layout       0.000000
42            Hanumanthanagar, Bengaluru       0.000000
43                             Hebbagodi       0.000000
44                                Hebbal       0.000000
45                                 Hoodi       0.023256
46                              Horamavu       0.000000
47                              Hulimavu       0.016949
48                           Immadihalli       0.027778
49                           Indiranagar       0.000000
50                              Ittamadu       0.025641
51                           J. P. Nagar       0.020000
52                                Jakkur       0.000000
53                             Jalahalli       0.125000
54                  Jayanagar, Bangalore       0.000000
55                    Jeevanbheema Nagar       0.010000
56                                Jigani       0.000000
57                         Kaggadasapura       0.000000
58                          Kalasipalyam       0.010989
59                           Kalikanagar       0.000000
60                               Kalkere       0.000000
61                          Kalyan Nagar       0.000000
62                         Kamakshipalya       0.000000
63                          Kammanahalli       0.030769
64                               Kengeri       0.000000
65                           Kodigehalli       0.000000
66                  Kodihalli, Bangalore       0.000000
67                           Konanakunte       0.000000
68                            Koppa gate       0.000000
69                           Koramangala       0.000000
70                      Krishnarajapuram       0.02

###  Cluster Neighborhoods

Run k-means to cluster the neighborhoods in Bhopal into 4 clusters

In [31]:
# set number of clusters
kclusters = 3

BLR_clustering = BLR_mall.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(BLR_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 1, 0, 0, 0, 0, 0, 0], dtype=int32)

In [32]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
BLR_merged = BLR_mall.copy()

# add clustering labels
BLR_merged["Cluster Labels"] = kmeans.labels_

In [33]:
BLR_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
BLR_merged.head()

Neighborhood  Shopping Mall  Cluster Labels
0      Adugodi       0.010000               0
1  Ananthnagar       0.000000               0
2   Anjanapura       0.000000               0
3      Arekere       0.025974               1
4  Austin Town       0.010000               0

In [34]:
# merge bhopal_grouped with bhopal_data to add latitude/longitude for each neighborhood
BLR_merged = BLR_merged.join(df.set_index("Neighborhood"), on="Neighborhood")

print(BLR_merged.shape)
BLR_merged.head() # check the last columns!

(128, 5)


Neighborhood  Shopping Mall  Cluster Labels  Latitude  Longitude
0      Adugodi       0.010000               0  12.94402   77.60800
1  Ananthnagar       0.000000               0  12.95408   77.54135
2   Anjanapura       0.000000               0  12.85811   77.55909
3      Arekere       0.025974               1  12.88568   77.59668
4  Austin Town       0.010000               0  12.96348   77.61297

In [93]:
# sort the results by Cluster Labels
print(BLR_merged.shape)
BLR_merged.sort_values(["Cluster Labels"], inplace=True)
BLR_merged

(128, 5)


Neighborhood  Shopping Mall  Cluster Labels  \
0                                Adugodi       0.010000               0   
85                            Nagarbhavi       0.000000               0   
83                         Murugeshpalya       0.000000               0   
82                Murphy Town, Bangalore       0.011236               0   
81                           Milk Colony       0.010000               0   
80                             Mathikere       0.000000               0   
79                        Mariyannapalya       0.000000               0   
74                              Madiwala       0.010000               0   
71                    Kumaraswamy Layout       0.000000               0   
69                           Koramangala       0.000000               0   
68                            Koppa gate       0.000000               0   
87                          Nayandahalli       0.000000               0   
67                           Konanakunte       0.000000               0   
65                           Kodigehalli       0.000000               0   
64                               Kengeri       0.000000               0   
126                            Yelahanka       0.000000               0   
62                         Kamakshipalya       0.000000               0   
61                          Kalyan Nagar       0.000000               0   
60                               Kalkere       0.000000               0   
59                           Kalikanagar       0.000000               0   
58                          Kalasipalyam       0.011765               0   
57                         Kaggadasapura       0.000000               0   
56                                Jigani       0.000000               0   
66                  Kodihalli, Bangalore       0.000000               0   
89                     Palace Guttahalli       0.010204               0   
91                          Puttenahalli       0.010000               0   
92                           R. T. Nagar       0.000000               0   
124                        Wilson Garden       0.000000               0   
122                           Vyalikaval       0.000000               0   
120               Vijayanagar, Bangalore       0.000000               0   
119                       Vidyaranyapura       0.000000               0   
118                        Vasanth Nagar       0.010000               0   
116                          Uttarahalli       0.000000               0   
114                      Thyagarajanagar       0.000000               0   
113                              Thindlu       0.000000               0   
110                            Sulikunte       0.000000               0   
109                      Suddaguntepalya       0.010753               0   
108  Statue of Queen Victoria, Bangalore       0.000000               0   
107      Statue of Edward VII, Bangalore       0.010000               0   
104                         Shikaripalya       0.000000               0   
103                        Seshadripuram       0.010000               0   
102                          Sanjaynagar       0.000000               0   
101                       Sahakara Nagar       0.000000               0   
100                       Sadashivanagar       0.000000               0   
99                         Richmond Town       0.010000               0   
98                      Ramanjaneyanagar       0.000000               0   
97                      Ramamurthy Nagar       0.000000               0   
96                      Ramagondanahalli       0.000000               0   
94       Rajarajeshwari Nagar, Bangalore       0.000000               0   
93                           Rajajinagar       0.011364               0   
55                    Jeevanbheema Nagar       0.010000               0   
54                  Jayanagar, Bangalore       0.000000               0   
127                          Yeswanthpur       0.0000

In [35]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(BLR_merged['Latitude'], BLR_merged['Longitude'], BLR_merged['Neighborhood'], BLR_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [36]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

### Examine Clusters

#### Cluster 0

In [37]:
BLR_merged.loc[BLR_merged['Cluster Labels'] == 0]

Neighborhood  Shopping Mall  Cluster Labels  \
0                                Adugodi       0.010000               0   
1                            Ananthnagar       0.000000               0   
2                             Anjanapura       0.000000               0   
4                            Austin Town       0.010000               0   
5                             BTM Layout       0.011905               0   
6                            Babusapalya       0.000000               0   
7               Bagalur, Bangalore Urban       0.000000               0   
8                          Bahubalinagar       0.000000               0   
9                           Banashankari       0.010000               0   
10                             Banaswadi       0.000000               0   
11                          Basavanagudi       0.000000               0   
12                     Basaveshwaranagar       0.000000               0   
13                             Bellandur       0.011236               0   
14                          Bharathnagar       0.000000               0   
15                           Bilekahalli       0.010753               0   
16                          Bommanahalli       0.000000               0   
17                           Bommasandra       0.000000               0   
19                       Byatarayanapura       0.000000               0   
20                        CV Raman Nagar       0.010000               0   
21                            Carmelaram       0.000000               0   
22                            Chamrajpet       0.012500               0   
23                            Chandapura       0.000000               0   
29                   Devarachikkanahalli       0.000000               0   
30                        Dollars Colony       0.000000               0   
31                                Domlur       0.000000               0   
32                               Ejipura       0.000000               0   
33                       Electronic City       0.000000               0   
35                         Gandhi Bazaar       0.000000               0   
36               Gandhi Nagar, Bangalore       0.000000               0   
37                 Ganganagar, Bangalore       0.000000               0   
38                             Girinagar       0.000000               0   
40                            HBR Layout       0.000000               0   
41                            HSR Layout       0.000000               0   
42            Hanumanthanagar, Bengaluru       0.000000               0   
43                             Hebbagodi       0.000000               0   
44                                Hebbal       0.000000               0   
46                              Horamavu       0.000000               0   
49                           Indiranagar       0.000000               0   
52                                Jakkur       0.000000               0   
54                  Jayanagar, Bangalore       0.000000               0   
55                    Jeevanbheema Nagar       0.010000               0   
56                                Jigani       0.000000               0   
57                         Kaggadasapura       0.000000               0   
58                          Kalasipalyam       0.010989               0   
59                           Kalikanagar       0.000000               0   
60                               Kalkere       0.000000               0   
61                          Kalyan Nagar       0.000000               0   
62                         Kamakshipalya       0.000000               0   
64                               Kengeri       0.000000               0   
65                           Kodigehalli       0.000000               0   
66                  Kodihalli, Bangalore       0.000000               0   
67                           Konanakunte       0.000000               0   
68                            Koppa gate       0.0000

#### cluster 1

In [38]:
BLR_merged.loc[BLR_merged['Cluster Labels'] == 1]

Neighborhood  Shopping Mall  Cluster Labels   Latitude  \
3                    Arekere       0.025974               1  12.885680   
18               Brookefield       0.023810               1  12.993330   
24                  Chickpet       0.013889               1  12.970150   
25            Chikkalasandra       0.027778               1  12.909950   
26                Cooke Town       0.027778               1  13.003630   
27       Cox Town, Bangalore       0.027778               1  12.995940   
34    Fraser Town, Bangalore       0.021505               1  12.998940   
39              Gowdanapalya       0.036364               1  12.909680   
45                     Hoodi       0.023256               1  12.991980   
47                  Hulimavu       0.016949               1  12.880640   
48               Immadihalli       0.027778               1  12.966860   
50                  Ittamadu       0.025641               1  12.923440   
51               J. P. Nagar       0.020000               1  12.908310   
63              Kammanahalli       0.030769               1  13.014300   
70          Krishnarajapuram       0.029851               1  13.000390   
72              Kundalahalli       0.023256               1  12.967520   
73            Lingarajapuram       0.029412               1  13.005480   
75   Mahadevapura, Bangalore       0.021739               1  12.994090   
76        Mahalakshmi Layout       0.016393               1  13.016350   
77               Malleswaram       0.020000               1  13.006322   
78              Marathahalli       0.014085               1  12.954660   
84             Muthyalanagar       0.025641               1  13.041030   
86            Nandini Layout       0.023529               1  13.014810   
88           Padmanabhanagar       0.027778               1  12.918140   
90                    Peenya       0.045455               1  13.031850   
105  Shivajinagar, Bangalore       0.020000               1  12.987200   
111             Tannery Road       0.018182               1  13.007681   
112               Taverekere       0.020000               1  12.922450   
115                   Ulsoor       0.020000               1  12.989080   
117                  Varthur       0.033333               1  12.943480   
121               Vimanapura       0.021277               1  13.002540   
123    Whitefield, Bangalore       0.028169               1  12.979380   
125           Yelachenahalli       0.021277               1  12.900440   

     Longitude  
3    77.596680  
18   77.661230  
24   77.575890  
25   77.550510  
26   77.622830  
27   77.626440  
34   77.612760  
39   77.556750  
45   77.715060  
47   77.601470  
48   77.761580  
50   77.542840  
51   77.590240  
63   77.636850  
70   77.683680  
72   77.715000  
73   77.625970  
75   77.666330  
76   77.544810  
77   77.568416  
78   77.707520  
84   77.551480  
86   77.538910  
88   77.559400  
90   77.526790  
105  77.604010  
111  77.612868  
112  77.610330  
115  77.627950  
117  77.747030  
121  77.667640  
123  77.733720  
125  77.568650

#### Cluster 2

In [39]:
BLR_merged.loc[BLR_merged['Cluster Labels'] ==2]

Neighborhood  Shopping Mall  Cluster Labels  Latitude  Longitude
28            Dasarahalli       0.100000               2  13.04224   77.51507
53              Jalahalli       0.125000               2  13.05450   77.52658
95        Ramachandrapura       0.083333               2  13.06124   77.55112
106  Siddapura, Bangalore       0.061538               2  12.95613   77.73196

### Observation

Most of the shopping malls are concentrated in the central area of Bengaluru city, with the highest number in cluster 2 and moderate number in cluster 1. On the other hand, cluster 0 has very low number to totally no shopping mall in the neighborhoods. This represents a great opportunity and high potential areas to open new shopping malls as there is very little to no competition from existing malls. Meanwhile, shopping malls in cluster 2 are likely suffering from intense competition due to oversupply and high concentration of shopping malls. From another perspective, this also shows that the oversupply of shopping malls mostly happened in the central area of the city, with the suburb area still have very few shopping malls. Therefore, this project recommends property developers to capitalize on these findings to open new shopping malls in neighborhoods in cluster 0 with little to no competition. Property developers with unique selling propositions to stand out from the competition can also open new shopping malls in neighborhoods in cluster 2 & 3 with moderate competition. Lastly, property developers are advised to avoid neighborhoods in cluster 1 which already have high concentration of shopping malls and suffering from intense competition.